In [15]:
import geopandas as gpd
import osmnx as ox
import folium
from shapely.geometry import shape


cycle_graph = ox.load_graphml("../data/valencia_cycling_network.graphml")

## Fuentes de agua pública

In [16]:
def get_fuentes_de_agua_publica(valencian_data):
    """
    Extract public water fountains from the Valencian data.

    Parameters:
        valencian_data (DataFrame): A DataFrame containing Valencian data.

    Returns:
        GeoDataFrame: A GeoDataFrame containing the public water fountains.
    """
    # Filter the DataFrame for public water fountains
    fountains = valencian_data[
        valencian_data["dataset"] == "fonts-daigua-publica-fuentes-de-agua-publica"
    ]

    # Convert the DataFrame to a GeoDataFrame
    gdf = gpd.GeoDataFrame(fountains, geometry=fountains["geo_shape"].apply(shape))
    gdf.set_crs(epsg=4326, inplace=True)  # Set the coordinate reference system

    return gdf

In [17]:
import pandas as pd


def get_nearest_water_fountain(graph, water_fountains_gdf):
    """
    Find the nearest point in the graph to each public water fountain.

    Parameters:
        graph: The cycling network graph.
        water_fountains_gdf (GeoDataFrame): A GeoDataFrame containing public water fountains.

    Returns:
        GeoDataFrame: A GeoDataFrame with the nearest points in the graph to each public water fountain.
    """
    nearest_points = []
    distances = []
    for _, row in water_fountains_gdf.iterrows():
        point = row.geometry
        nearest_node = ox.distance.nearest_nodes(graph, point.x, point.y)
        distance = ox.distance.euclidean(
            point.y,
            point.x,
            graph.nodes[nearest_node]["y"],
            graph.nodes[nearest_node]["x"],
        )
        nearest_points.append(nearest_node)
        distances.append(distance)

    water_fountains_gdf["nearest_node"] = nearest_points
    water_fountains_gdf["distance_to_nearest_node"] = distances
    return water_fountains_gdf

In [18]:
fuentes_publicas = pd.read_csv("../data/fonts_publiques.csv")

In [19]:
val = fuentes_publicas["geo_shape"].iloc[0]
print(val, type(val))


{'type': 'Feature', 'geometry': {'coordinates': [-0.3245649933146064, 39.470317839583906], 'type': 'Point'}, 'properties': {}} <class 'str'>


In [20]:
import ast

# parsear la columna de strings a dict, luego a geometría Shapely
fuentes_publicas["geometry"] = fuentes_publicas["geo_shape"].apply(
    lambda s: shape(ast.literal_eval(s))
)


In [21]:
def get_valenbisi_stations(valenbisi_data):
    """
    Extract Valenbisi stations from the Valenbisi data.

    Parameters:
        valenbisi_data (DataFrame): A DataFrame containing Valenbisi data.

    Returns:
        GeoDataFrame: A GeoDataFrame containing the Valenbisi stations.
    """

    # Convert the DataFrame to a GeoDataFrame
    gdf = gpd.GeoDataFrame(valenbisi_data, geometry=valenbisi_data["geometry"])
    gdf.set_crs(epsg=4326, inplace=True)  # Set the coordinate reference system

    return gdf

In [22]:
fuentes_publicas_gpd = get_valenbisi_stations(fuentes_publicas)

In [23]:
fuentes_publicas_gpd

objectid                                  calle codigo  \
0           5  PASEO MARITIMO/HISTORIADOR COLOMA--2ª   1151   
1           9   BULEVAR SUR - BARRACA AUSIAS MARCH 1   1040   
2          11                      PLAZA DEL MERCADO    110   
3          17               JARDIN PLAZA DE LA REINA    104   
4          22            CEMENTERIO GENERAL SEC 20-1   C121   
..        ...                                    ...    ...   
827       230          PLATERO SUAREZ /CALLE SAGUNTO    509   
828       267                AVDA. BLASCO IBAÑEZ, 96   1312   
829       276          PLAZA JOAQUIN MUÑOZ PEIRATS 1   1607   
830       150           PL DOCTOR LORENZO DE LA FLOR   1155   
831       159          CEMENTERIO GENERAL SEC 6 IZDA   C113   

                                                  foto  \
0    http://mapas.valencia.es/WebsMunicipales/layar...   
1    http://mapas.valencia.es/WebsMunicipales/layar...   
2    http://mapas.valencia.es/WebsMunicipales/layar...   
3    http://mapas.valencia.es/WebsMunicipales/layar...   
4    http://mapas.valencia.es/WebsMunicipales/layar...   
..                                                 ...   
827  http://mapas.valencia.es/WebsMunicipales/layar...   
828  http://mapas.valencia.es/WebsMunicipales/layar...   
829  http://mapas.valencia.es/WebsMunicipales/layar...   
830  http://mapas.valencia.es/WebsMunicipales/layar...   
831  http://mapas.valencia.es/WebsMunicipales/layar...   

                                             geo_shape  \
0    {'type': 'Feature', 'geometry': {'coordinates'...   
1    {'type': 'Feature', 'geometry': {'coordinates'...   
2    {'type': 'Feature', 'geometry': {'coordinates'...   
3    {'type': 'Feature', 'geometry': {'coordinates'...   
4    {'type': 'Feature', 'geometry': {'coordinates'...   
..                                                 ...   
827  {'type': 'Feature', 'geometry': {'coordinates'...   
828  {'type': 'Feature', 'geometry': {'coordinates'...   
829  {'type': 'Feature', 'geometry': {'coordinates'...   
830  {'type': 'Feature', 'geometry': {'coordinates'...   
831  {'type': 'Feature', 'geometry': {'coordinates'...   

                                          geo_point_2d  \
0    {'lon': -0.3245649933146064, 'lat': 39.4703178...   
1    {'lon': -0.37167000776736375, 'lat': 39.445251...   
2    {'lon': -0.37922498535436144, 'lat': 39.474571...   
3    {'lon': -0.37553501058701816, 'lat': 39.474624...   
4    {'lon': -0.3986200087544989, 'lat': 39.4429817...   
..                                                 ...   
827  {'lon': -0.37407299938987454, 'lat': 39.485198...   
828  {'lon': -0.35000500025418557, 'lat': 39.474304...   
829  {'lon': -0.3951179978157639, 'lat': 39.4869956...   
830  {'lon': -0.33100999912996454, 'lat': 39.469399...   
831  {'lon': -0.3980959950145709, 'lat': 39.4459724...   

                      geometry  
0    POINT (-0.32456 39.47032)  
1    POINT (-0.37167 39.44525)  
2    POINT (-0.37922 39.47457)  
3    POINT (-0.37554 39.47462)  
4    POINT (-0.39862 39.44298)  
..                         ...  
827   POINT (-0.37407 39.4852)  
828   POINT (-0.35001 39.4743)  
829    POINT (-0.39512 39.487)  
830   POINT (-0.33101 39.4694)  
831   POINT (-0.3981 39.44597)  

[832 rows x 7 columns]

In [24]:
def create_map_with_fonts(graph, stations_gdf, title):
    """
    Create a folium map with the cycling network and Valenbisi stations.

    Parameters:
        graph: The cycling network graph.
        stations_gdf (GeoDataFrame): A GeoDataFrame containing Valenbisi stations.
        title (str): The title of the map.

    Returns:
        folium.Map: A folium map object.
    """
    m = folium.Map(
        location=[39.4699, -0.3763],  # Centered on Valencia
        zoom_start=13,
        tiles="OpenStreetMap",
    )
    # for _, row in stations_gdf.iterrows():
    #     folium.Marker(
    #         location=[row.geometry.y, row.geometry.x],
    #         popup=row["address"],
    #         icon=folium.Icon(color="red"),
    #     ).add_to(m)

    # Add the cycling network edges to the map
    for t in graph.edges(data=True):
        ini, fin, info = t
        start = (graph.nodes[ini]["y"], graph.nodes[ini]["x"])
        end = (graph.nodes[fin]["y"], graph.nodes[fin]["x"])
        folium.PolyLine(
            locations=[start, end], color="blue", weight=2, opacity=0.8
        ).add_to(m)
    for _, row in stations_gdf.iterrows():
        folium.Marker(
            location=[row.geometry.y, row.geometry.x],
            popup=row["calle"],
            icon=folium.Icon(color="blue", icon="tint", prefix="fa"),
        ).add_to(m)
    m.get_root().html.add_child(folium.Element(f"<h3>{title}</h3>"))
    return m


# Create maps with Valenbisi stations
# walk_map = create_map_with_stations(
#     walk_graph, geovalenbisi_walk, "Walking Network with Valenbisi Stations"
# )

cycle_map = create_map_with_fonts(
    cycle_graph, fuentes_publicas_gpd, "Cycling Network with Valenbisi Stations"
)

cycle_map

In [25]:
# recibo una ruta de nodos y la distancia entre dos puntos, lo divido en segmentos y entre esos puntos busco las fuentes más cercanas, no más de una por segemento, que no se repitam y que estén a menos de 50 metros de la ruta
import osmnx as ox
import numpy as np


def get_nearest_water_fountains_on_route(
    graph, distancia, route_nodes, type_displacement, temperatura
):
    """
    Find the nearest public water fountains along a given route.

    Parameters:
        graph: The cycling network graph.
        route_nodes (list): A list of nodes representing the route.
        max_distance (float): The maximum distance from the route to consider a fountain.

    Returns:
        list: A list of dictionaries containing the fountain node and its distance from the route.
    """
    fountains = []

    start_node = route_nodes[0]
    end_node = route_nodes[-1]
    # Get the coordinates of the start and end nodes
    start_coords = (graph.nodes[start_node]["y"], graph.nodes[start_node]["x"])
    end_coords = (graph.nodes[end_node]["y"], graph.nodes[end_node]["x"])
    frecuencia_paradas_por_temperatura = {
        "frio": {
            "min_temp": -50,  # Valor mínimo (inferior a 10°C)
            "max_temp": 10,
            "Caminando": 7,  # minutos parar caminar
            "En Bicicleta": 12,  # minutos parar bicileta
        },
        "ideal": {
            "min_temp": 15,
            "max_temp": 25,
            "Caminando": 5,  # minutos parar caminar
            "En Bicicleta": 9,  # minutos parar bicileta
        },
        "calor_extremo": {
            "min_temp": 30,
            "max_temp": 50,  # Valor máximo (superior a 30°C)
            "Caminando": 3,  # minutos parar caminar
            "En Bicicleta": 6,  # minutos parar bicileta
        },
    }

    def obtener_frecuencia_paradas():
        if temperatura < 10:
            return frecuencia_paradas_por_temperatura["frio"][type_displacement]
        elif 15 <= temperatura <= 25:
            return frecuencia_paradas_por_temperatura["ideal"][type_displacement]
        elif temperatura > 30:
            return frecuencia_paradas_por_temperatura["calor_extremo"][
                type_displacement
            ]
        else:
            return False

    # Ejemplo de uso:

    # Calculate the midpoint of the segment
    mid_coords = (
        (start_coords[0] + end_coords[0]) / 2,
        (start_coords[1] + end_coords[1]) / 2,
    )

    if type_displacement == "Caminando":
        max_distance = 150
        velocidad_cam = 1  # m/s al haber semaforos, normalmente se camina a 1.4 m/s
        frecuencia_paradas = obtener_frecuencia_paradas()

        if frecuencia_paradas is not False:
            n_paradas = int(
                distancia / (velocidad_cam * 60 * frecuencia_paradas)
            )  # minutos de parada, cada cuanto parar
            if n_paradas > 0:
                print(f"Paradas: {n_paradas}")
                distancias_paradas = np.linspace(0, distancia, n_paradas + 1)
                for dist in distancias_paradas[1:]:  # Saltamos el 0 inicial
                    print(f"Distancia: {dist:.2f} metros")
                    # Calculate the coordinates of the point at the given distance
                    mid_coords = (
                        start_coords[0]
                        + (end_coords[0] - start_coords[0]) * (dist / distancia),
                        start_coords[1]
                        + (end_coords[1] - start_coords[1]) * (dist / distancia),
                    )
                    nearest_fountain = ox.distance.nearest_nodes(
                        graph, mid_coords[1], mid_coords[0]
                    )
                    # Calculate the distance to the nearest fountain
                    node_data = graph.nodes[nearest_fountain]

                    start = (node_data["y"], node_data["x"])
                    end = (float(mid_coords[0]), float(mid_coords[1]))
                    distance = get_distance(start, end)
                    print(f"Distancia a la fuente: {distance:.2f} metros")
                    if distance <= max_distance:
                        fountains.append(nearest_fountain)
                        print(
                            f"Fuente encontrada: {nearest_fountain} a {distance:.2f} metros de la ruta"
                        )

    elif type_displacement == "En Bicicleta" or type_displacement == "En ValenBisi":
        if type_displacement == "En ValenBisi":
            type_displacement = "En Bicicleta"

        max_distance = 200
        velocidad_bic = 2.6  # m/s, velocidad media en bicicleta con semaforos, normalmente se va a ~4 m/s
        frecuencia_paradas = obtener_frecuencia_paradas()

        if frecuencia_paradas is not False:
            n_paradas = int(
                distancia / (velocidad_bic * 60 * frecuencia_paradas)
            )  # minutos de parada, cada cuanto parar
            if n_paradas > 0:
                print(f"Paradas: {n_paradas}")
                distancias_paradas = np.linspace(0, distancia, n_paradas + 1)
                for dist in distancias_paradas[1:]:  # Saltamos el 0 inicial
                    print(f"Distancia: {dist:.2f} metros")
                    # Calculate the coordinates of the point at the given distance
                    mid_coords = (
                        start_coords[0]
                        + (end_coords[0] - start_coords[0]) * (dist / distancia),
                        start_coords[1]
                        + (end_coords[1] - start_coords[1]) * (dist / distancia),
                    )
                    nearest_fountain = ox.distance.nearest_nodes(
                        graph, mid_coords[1], mid_coords[0]
                    )
                    # Calculate the distance to the nearest fountain
                    node_data = graph.nodes[nearest_fountain]

                    start = (node_data["y"], node_data["x"])
                    end = (float(mid_coords[0]), float(mid_coords[1]))
                    distance = get_distance(start, end)
                    print(f"Distancia a la fuente: {distance:.2f} metros")
                    if distance <= max_distance:
                        fountains.append(nearest_fountain)
                        print(
                            f"Fuente encontrada: {nearest_fountain} a {distance:.2f} metros de la ruta"
                        )

    return fountains

In [26]:
import osmnx as ox
import numpy as np
from geopy.distance import geodesic


def get_distance(coord1, coord2):
    return geodesic(coord1, coord2).meters


def get_nearest_water_fountains_on_route(
    graph, distancia, route_nodes, type_displacement, temperatura
):
    fountains_found = set()
    fountain_results = []

    # Definir velocidades y frecuencias según temperatura
    frecs = {
        "frio": {"min": -50, "max": 10, "Caminando": 7, "En Bicicleta": 12},
        "ideal": {"min": 15, "max": 25, "Caminando": 5, "En Bicicleta": 9},
        "calor_extremo": {"min": 30, "max": 50, "Caminando": 3, "En Bicicleta": 6},
    }

    def get_frecuencia():
        for clima, rango in frecs.items():
            if rango["min"] <= temperatura <= rango["max"]:
                return rango[type_displacement]
        return None

    # Velocidades en m/s
    velocidad = 1 if type_displacement == "Caminando" else 2.6
    max_dist = 150 if type_displacement == "Caminando" else 200
    if type_displacement == "En ValenBisi":
        type_displacement = "En Bicicleta"

    frecuencia_paradas = get_frecuencia()
    if frecuencia_paradas is None:
        return []

    # Calcular puntos a lo largo de toda la ruta
    n_paradas = int(distancia / (velocidad * 60 * frecuencia_paradas))
    if n_paradas == 0:
        return []

    # Convertir ruta a coordenadas
    route_coords = [(graph.nodes[n]["y"], graph.nodes[n]["x"]) for n in route_nodes]
    cumulative_distance = [0]

    # Calcular distancias acumuladas para interpolar
    for i in range(1, len(route_coords)):
        seg_dist = get_distance(route_coords[i - 1], route_coords[i])
        cumulative_distance.append(cumulative_distance[-1] + seg_dist)

    # Distancias a las que buscar fuentes
    sample_dists = np.linspace(0, cumulative_distance[-1], n_paradas + 1)[1:]

    for target_dist in sample_dists:
        for i in range(1, len(cumulative_distance)):
            if cumulative_distance[i] >= target_dist:
                ratio = (target_dist - cumulative_distance[i - 1]) / (
                    cumulative_distance[i] - cumulative_distance[i - 1]
                )
                lat1, lon1 = route_coords[i - 1]
                lat2, lon2 = route_coords[i]
                mid_lat = lat1 + ratio * (lat2 - lat1)
                mid_lon = lon1 + ratio * (lon2 - lon1)

                nearest_node = ox.distance.nearest_nodes(graph, mid_lon, mid_lat)
                coord_node = (
                    graph.nodes[nearest_node]["y"],
                    graph.nodes[nearest_node]["x"],
                )
                dist_to_mid = get_distance((mid_lat, mid_lon), coord_node)

                if dist_to_mid <= max_dist and nearest_node not in fountains_found:
                    fountains_found.add(nearest_node)
                    fountain_results.append(nearest_node)
                break  # saltamos al siguiente target_dist tras primer match

    return fountain_results


In [27]:
import math


def get_distance(start, end):
    """
    Calculate the distance between two geographic points.

    Parameters:
        start (tuple): (lat, lon) in decimal degrees.
        end   (tuple): (lat, lon) in decimal degrees.

    Returns:
        deg_dist (float): Euclidean distance in decimal degrees.
        gc_dist_m (float): Great-circle distance in meters.
    """
    lat1, lon1 = map(math.radians, start)
    lat2, lon2 = map(math.radians, end)

    # 2. Haversine (great-circle) in meters
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = (
        math.sin(dlat / 2) ** 2
        + math.cos(lat1) * math.cos(lat2) * math.sin(dlon / 2) ** 2
    )
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    R = 6371000  # Earth radius in meters
    gc_dist_m = R * c

    return gc_dist_m

In [ ]:
def get_route(start, end, graph):
    """
    Get the route between two nodes in the graph.

    Parameters:
        start(tuple): Tuple of coordenates for the start point.
        end: Tuple of coordinates for the end point.
        graph: The cycling network graph.

    Returns:
        list: A list of nodes representing the route.
    """
    from_node = ox.distance.nearest_nodes(graph, start[1], start[0])
    to_node = ox.distance.nearest_nodes(graph, end[1], end[0])
    distancia = get_distance(
        start, end
    )  # [1]  # Get the great-circle distance in meters
    route = ox.shortest_path(graph, from_node, to_node, weight="length")
    return route, distancia


# Example usage
start = (39.4699, -0.3763)  # Example start coordinates (Valencia center)
end = (39.456934, -0.363584)  # Example end coordinates (somewhere else in Valencia)
route, distancia = get_route(start, end, cycle_graph)

In [29]:
fountains_on_route = get_nearest_water_fountains_on_route(
    cycle_graph, distancia, route, "Caminando", 20
)
fountains_on_route

[6524105932, 12438933296, 10896175585, 1307522797, 1827083416]